# Business Data Challenge - Team 1

In [1]:
import pandas as pd
import numpy as np
import os
import s3fs
import re

Configuration de l'accès aux données

In [2]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

# Exemple sur Company 1

## Chargement données

In [3]:
BUCKET = "bdc2324-data/1"
liste_database = fs.ls(BUCKET)

In [5]:
liste_database_select = ['suppliers', 'ticket', 'purchase', 'consumption', 'type_ofs']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_database_filtered = [element for element in liste_database if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_database_filtered)

In [6]:
# loop to create dataframes from liste
files_path = liste_database

client_number = files_path[0].split("/")[1]
df_prefix = "df" + str(client_number) + "_"

for i in range(len(files_path)) :
    current_path = files_path[i]
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)
        # the pattern of the name is df1xxx
        nom_dataframe = df_prefix + re.search(r'\/(\d+)\/(\d+)([a-zA-Z_]+)\.csv$', current_path).group(3)
        globals()[nom_dataframe] = df

<<<<<<< local <modified: >
/tmp/ipykernel_445/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)
/tmp/ipykernel_15285/4081512283.py:10: DtypeWarning: Columns (1) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in)
>>>>>>> remote <modified: >


## customersplus.csv

In [22]:
a = pd.DataFrame(df1_customersplus.info())

In [31]:
def info_colonnes_dataframe(df):
    # Créer une liste pour stocker les informations sur chaque colonne
    infos_colonnes = []

    # Parcourir les colonnes du DataFrame
    for nom_colonne, serie in df.items():  # Utiliser items() au lieu de iteritems()
        # Calculer le taux de valeurs manquantes
        taux_na = serie.isna().mean() * 100

        # Ajouter les informations à la liste
        infos_colonnes.append({
            'Nom_colonne': nom_colonne,
            'Type_colonne': str(serie.dtype),
            'Taux_NA': taux_na
        })

    # Créer une nouvelle DataFrame à partir de la liste d'informations
    df_infos_colonnes = pd.DataFrame(infos_colonnes)

    return df_infos_colonnes

In [35]:
def cleaning_date(df, column_name):
    """
    Nettoie la colonne spécifiée du DataFrame en convertissant les valeurs en datetime avec le format ISO8601.

    Parameters:
    - df: DataFrame
        Le DataFrame contenant la colonne à nettoyer.
    - column_name: str
        Le nom de la colonne à nettoyer.

    Returns:
    - DataFrame
        Le DataFrame modifié avec la colonne nettoyée.
    """
    df[column_name] = pd.to_datetime(df[column_name], utc = True, format = 'ISO8601')
    return df

In [32]:
a = info_colonnes_dataframe(df1_customersplus)

In [33]:
a

In [16]:
a = pd.DataFrame(df1_customersplus.isna().sum()/len(df1_customersplus)*100)

In [40]:
# Selection des variables
df1_customersplus_clean = df1_customersplus.copy()

cleaning_date(df1_customersplus_clean, 'first_buying_date')
cleaning_date(df1_customersplus_clean, 'last_visiting_date')

df1_customersplus_clean.drop(['lastname', 'firstname', 'email', 'civility', 'note', 'created_at', 'updated_at', 'deleted_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode', 'last_visiting_date'], axis = 1, inplace=True)
df1_customersplus_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)



## tickets.csv

In [6]:
df1_tickets

In [7]:
df1_tickets.info()

In [8]:
df1_tickets.isna().sum()/len(df1_tickets)*100

In [9]:
# Selection des variables
df1_tickets_clean = df1_tickets.drop(['lastname', 'firstname', 'email', 'created_at', 'updated_at', 'extra', 'reference', 'extra_field', 'identifier', 'need_reload', 'preferred_category', 'preferred_supplier', 'preferred_formula', 'zipcode'], axis = 1, inplace=True)
df1_tickets_clean.rename(columns = {'id' : 'customer_id'}, inplace = True)

## suppliers.csv

In [10]:
df1_suppliers

In [11]:
df1_suppliers.info()

In [12]:
df1_suppliers.isna().sum()/len(df1_suppliers)*100

In [13]:
# Selection des variables
df1_suppliers_clean = df1_suppliers[['id', 'name']]
df1_suppliers_clean.rename(columns = {'name' : 'supplier_name'}, inplace = True)

In [14]:
df1_suppliers_clean

## type_ofs.csv

In [15]:
df1_type_ofs

In [16]:
df1_type_ofs.info()

In [17]:
# Selection des variables
df1_type_ofs_clean = df1_type_ofs[['id', 'name', 'children']]
df1_type_ofs_clean.rename(columns = {'name' : 'type_of_ticket_name'}, inplace = True)

## purchases.csv

In [18]:
df1_purchases

In [19]:
df1_purchases.info()

In [20]:
# Nettoyage purchase_date
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], utc = True)
df1_purchases['purchase_date'] = pd.to_datetime(df1_purchases['purchase_date'], format = 'ISO8601')

In [21]:
df1_purchases.info()

In [22]:
# Selection des variables
df1_purchases_clean = df1_purchases[['id', 'purchase_date', 'customer_id']]

## Fusion de l'ensemble des données billétiques

In [23]:
# Fusion avec fournisseurs
df1_ticket_information = pd.merge(df1_tickets_clean, df1_suppliers_clean, left_on = 'supplier_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['supplier_id', 'id'], axis = 1, inplace=True)

# Fusion avec type de tickets
df1_ticket_information = pd.merge(df1_ticket_information, df1_type_ofs_clean, left_on = 'type_of', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['type_of', 'id'], axis = 1, inplace=True)

# Fusion avec achats
df1_ticket_information = pd.merge(df1_ticket_information, df1_purchases_clean, left_on = 'purchase_id', right_on = 'id', how = 'inner')
df1_ticket_information.drop(['purchase_id', 'id'], axis = 1, inplace=True)

In [24]:
df1_ticket_information

# Utilisation de fonctions

In [51]:
# Créer un DataFrame exemple
df_not_clean = df1_campaign_stats[['opened_at']].head(20)

# Appliquer la fonction pour nettoyer la colonne 'purchase_date' de manière vectorisée
df_clean = cleaning_date(df_not_clean, 'opened_at')
df_clean.rename(columns = {'opened_at' : 'opened_at_clean'}, inplace = True)

test = pd.concat([df1_campaign_stats[['opened_at']].head(20), df_clean], axis=1)

test.info()

## Nettoyage, selection et fusion

In [23]:
df1_ticket_information

In [14]:
df1_ticket_information.info()

# Customer information

## Target area

In [8]:
# Target.csv cleaning
df1_targets_clean = df1_targets[["id", "target_type_id", "name"]]
df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)

# target_type cleaning
df1_target_types_clean = df1_target_types[["id","is_import","name"]].add_prefix("target_type_")

#customer_target_mappings cleaning
df1_customer_target_mappings_clean = df1_customer_target_mappings[["id", "customer_id", "target_id"]]

# Merge target et target_type
df1_targets_full = pd.merge(df1_targets_clean, df1_target_types_clean, left_on='target_type_id', right_on='target_type_id', how='inner')
df1_targets_full.drop(['target_type_id'], axis = 1, inplace=True)

# Merge
df1_targets_full = pd.merge(df1_customer_target_mappings_clean, df1_targets_full, left_on='target_id', right_on='target_id', how='inner')
df1_targets_full.drop(['target_id'], axis = 1, inplace=True)

/tmp/ipykernel_15285/2625134041.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1_targets_clean.rename(columns = {'id' : 'target_id' , 'name' : 'target_name'}, inplace = True)


In [62]:
df1_targets_test = df1_targets_full[['id', 'customer_id']].groupby(['customer_id']).count()
len(df1_targets_test[df1_targets_test['id'] > 1]) / len(df1_targets_test)

# 99,6% des 151 000 client visés sont catégorisés plusieurs fois et en moyenne 5 fois... 
df1_targets_test.mean()


In [10]:
df1_targets_full.head()

id  customer_id               target_name  target_type_is_import  \
0  1184824       645400  DDCP PROMO Réseau livres                  False   
1   210571         2412  DDCP PROMO Réseau livres                  False   
2   210572         4536  DDCP PROMO Réseau livres                  False   
3   210573         6736  DDCP PROMO Réseau livres                  False   
4   210574        38210  DDCP PROMO Réseau livres                  False   

       target_type_name  
0  manual_static_filter  
1  manual_static_filter  
2  manual_static_filter  
3  manual_static_filter  
4  manual_static_filter

In [14]:
# Catégorisation des target_name
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer
from nltk.probability import FreqDist

# Téléchargement des ressources nécessaires
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')



[nltk_data] Downloading package punkt to /home/onyxia/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/onyxia/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/onyxia/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [19]:
# Définition des fonctions de tokenisation, suppression des mots vides et lemmatisation
def preprocess_text(texte):
    # Concaténation des éléments de la liste en une seule chaîne de caractères
    texte_concat = ' '.join(texte)
    
    # Tokenisation des mots
    tokens = word_tokenize(texte_concat.lower())
    
    # Suppression des mots vides (stopwords)
    stop_words = set(stopwords.words('french'))
    filtered_tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatisation des mots
    lemmatizer = WordNetLemmatizer()
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]
    
    return lemmatized_tokens


# Appliquer le prétraitement à la colonne de texte
df1_targets_full['target_name_tokened'] = df1_targets_full['target_name'].apply(preprocess_text)

# Concaténer les listes de mots pour obtenir une liste de tous les mots dans le corpus
all_words = [word for tokens in df1_targets_full['target_name_tokened'] for word in tokens]

# Calculer la fréquence des mots
freq_dist = FreqDist(all_words)




Mots les plus fréquents:
consentement: 550777
optin: 463579
jeune: 155103
public: 155103
mediation: 150001


In [22]:
# Affichage des mots les plus fréquents
print("Mots les plus fréquents:")
for mot, freq in freq_dist.most_common(15):
    print(f"{mot}: {freq}")

Mots les plus fréquents:
consentement: 550777
optin: 463579
jeune: 155103
public: 155103
mediation: 150001
specialisee: 150001
b2c: 143432
optout: 97683
newsletter: 56022
(: 46084
): 46084
inscrits: 42296
nl: 42294
générale: 41037
generale: 40950


In [18]:
import pandas as pd
import nltk
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from nltk.stem import WordNetLemmatizer

# Téléchargement des ressources nécessaires
nltk.download('punkt')
nltk.download('stopwords')
nltk.download('wordnet')

# Création de la DataFrame d'exemple
data = {'texte': ["Le chat noir mange une souris.", "Le chien blanc aboie."]}
df = pd.DataFrame(data)

# Fonction pour prétraiter le texte
def preprocess_text(texte):
    # Concaténation des éléments de la liste en une seule chaîne de caractères
    texte_concat = ' '.join(texte)
    
    # Tokenisation des mots
    tokens = word_tokenize(texte_concat.lower())
    
    # Suppression des mots vides (stopwords)
    stop_words = set(stopwords.words('french'))
    filtered_tokens = [word for word in tokens if word not in stop_words]
    
    # Lemmatisation des mots
    lemmatizer = WordNetLemmatizer()
    lemmatized_tokens = [lemmatizer.lemmatize(word) for word in filtered_tokens]
    
    return lemmatized_tokens

# Appliquer la fonction de prétraitement à la colonne de texte
df['texte_preprocessed'] = df['texte'].apply(preprocess_text)

# Afficher le résultat
print(df)


                            texte  \
0  Le chat noir mange une souris.   
1           Le chien blanc aboie.   

                                 texte_preprocessed  
0  [e, h, a, o, i, r, a, g, e, u, e, o, u, r, i, .]  
1              [e, h, i, e, b, a, a, b, o, i, e, .]  


[nltk_data] Downloading package punkt to /home/onyxia/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package stopwords to /home/onyxia/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package wordnet to /home/onyxia/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


## Campaign area

In [52]:
# campaign_stats cleaning 
df1_campaign_stats_clean = df1_campaign_stats[["id", "campaign_id", "customer_id", "opened_at", "sent_at", "delivered_at"]]
cleaning_date(df1_campaign_stats_clean, 'opened_at')
cleaning_date(df1_campaign_stats_clean, 'sent_at')
cleaning_date(df1_campaign_stats_clean, 'delivered_at')

# campaigns cleaning
df1_campaigns_clean = df1_campaigns[["id", "name", "service_id", "sent_at"]].add_prefix("campaign_")
cleaning_date(df1_campaigns_clean, 'campaign_sent_at')

# Merge 
df1_campaigns_full = pd.merge(df1_campaign_stats_clean, df1_campaigns_clean, on = "campaign_id", how = "left")
df1_campaigns_full.drop(['campaign_id'], axis = 1, inplace=True)

In [53]:
df1_campaigns_full.info()

In [56]:
df1_campaigns_information

## Link area

In [37]:
df1_campaigns

In [38]:
df1_link_stats

## Exploration variables

In [7]:
# Fonction d'exploration pour suppliers.csv = label itr et commission inconnues
def suppliers_exploration(suppliers = None) : 
    
    # Taux de NaN pour ces colonnes
    label_na = suppliers['label'].isna().sum()/len(suppliers)*100
    itr_na = suppliers['itr'].isna().sum()/len(suppliers)*100
    commission_na = suppliers['commission'].isna().sum()/len(suppliers)*100

    suppliers_desc = pd.DataFrame({'nb_suppliers' : [suppliers['name'].nunique()],
                                  'label_na' : [label_na],
                                  'itr_na' : [itr_na],
                                  'commission_na' : [commission_na]})

    return suppliers_desc

In [8]:
df1_suppliers_desc = suppliers_exploration(suppliers = df1_suppliers)

In [9]:
df1_suppliers_desc

nb_suppliers  label_na  itr_na  commission_na
0             9     100.0   100.0          100.0

In [10]:
BUCKET = "bdc2324-data"
liste_folders = fs.ls(BUCKET)

liste_files = []
for company_folder in liste_folders : 
    liste_files.extend(fs.ls(company_folder))

In [11]:
liste_database_select = ['suppliers']

# Filtrer la liste pour les éléments contenant au moins un élément de la liste à tester
liste_suppliers = [element for element in liste_files if any(element_part in element for element_part in liste_database_select)]

# Afficher le résultat
print(liste_suppliers)

['bdc2324-data/1/1suppliers.csv', 'bdc2324-data/10/10suppliers.csv', 'bdc2324-data/101/101suppliers.csv', 'bdc2324-data/11/11suppliers.csv', 'bdc2324-data/12/12suppliers.csv', 'bdc2324-data/13/13suppliers.csv', 'bdc2324-data/14/14suppliers.csv', 'bdc2324-data/2/2suppliers.csv', 'bdc2324-data/3/3suppliers.csv', 'bdc2324-data/4/4suppliers.csv', 'bdc2324-data/5/5suppliers.csv', 'bdc2324-data/6/6suppliers.csv', 'bdc2324-data/7/7suppliers.csv', 'bdc2324-data/8/8suppliers.csv', 'bdc2324-data/9/9suppliers.csv']


In [32]:
# loop to create dataframes from file 2
def database_loading(database_name = None):
    files_path = database_name
    
    client_number = files_path.split("/")[1]
    df_prefix = "df" + str(client_number) + "_"
    
    current_path = files_path
    with fs.open(current_path, mode="rb") as file_in:
        df = pd.read_csv(file_in)

    return df, client_number

In [45]:
df_all = pd.DataFrame()

for link in liste_suppliers:
    
    df_supplier, tenant_id = database_loading(link)
    
    df_supplier['tenant_id'] = int(tenant_id)

    df_all = pd.concat([df_all, df_supplier], axis = 0)
    

In [63]:
# df_all[df_all['tenant_id'] == 101]['name'].unique()

In [66]:
liste_mots = ['en ligne', 'internet', 'web', 'net', 'vad', 'online'] 
# vad = vente à distance
df_all['name'] = df_all['name'].fillna('')

df_all['canal_vente_internet'] = df_all['name'].str.contains('|'.join(liste_mots), case=False).astype(int)


In [68]:
df_all.groupby('tenant_id')['canal_vente_internet'].max()

tenant_id
1      1
2      1
3      1
4      1
5      1
6      1
7      1
8      1
9      1
10     1
11     1
12     1
13     1
14     1
101    1
Name: canal_vente_internet, dtype: int64